In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import os
import sys
import warnings
from datetime import timedelta
from pandas.tseries.offsets import MonthEnd
import statsmodels.api as sm

import plotly.express as px
import plotly.graph_objects as go

In [2]:
def get_cpi():
    cpi = pd.read_excel('data/CPIAUCSL (1).xls')
    #cpi = pd.read_csv("T5YIE.csv")
    cpi.columns = ["date", 'CPI']
    cpi["date"] = pd.to_datetime(cpi["date"]) - timedelta(days=1)
    return cpi
    

def get_stocks():
    stocks = pd.read_csv("data/comp_stocks.csv")
    stocks["datadate"] = pd.to_datetime(stocks["datadate"])
    return stocks


def merge_cpi_stock(stocks, cpi):
    merged = pd.merge(stocks, cpi, how="left", left_on="MthCalDt", right_on="date")
    return merged

def bin_inflation_regimes(cpi, labels = ["deflation","low", "mid", "high"], bins = [-10, 0,1,3,20], value = "CPI", col = "Inflation"):
    cpi[col] = pd.cut(cpi[value],bins, labels=labels)
    return cpi


def get_percent_change(cpi):
    cpi["pct_change"] = cpi["CPI"].pct_change()
    return cpi

# get difference in inflation between two months
def get_inflation_diff(cpi, col = "diff", value = "CPI"):
    cpi[col] = cpi[value].diff()
    return cpi

In [3]:
cpi = get_cpi()
cpi = get_inflation_diff(cpi)
cpi = get_inflation_diff(cpi, col = "diff_of_diff", value = "diff")

In [4]:
cpi.dropna()

date      CPI     diff  diff_of_diff
2   1948-02-29  6.81818 -2.66378      -1.90365
3   1948-03-31  8.27273  1.45455       4.11833
4   1948-04-30  9.38497  1.11224      -0.34231
5   1948-05-31  9.37500 -0.00997      -1.12221
6   1948-06-30  9.76158  0.38658       0.39655
..         ...      ...      ...           ...
895 2022-07-31  8.22736 -0.18582       0.33399
896 2022-08-31  8.21485 -0.01251       0.17331
897 2022-09-30  7.76249 -0.45236      -0.43985
898 2022-10-31  7.13535 -0.62714      -0.17478
899 2022-11-30  6.44494 -0.69041      -0.06327

[898 rows x 4 columns]

In [5]:
stocks = get_stocks()
# remove stocks with above 500 trt1m
stocks = stocks[stocks["trt1m"] < 1000]

# remove stocks with below -100 trt1m
stocks = stocks[stocks["trt1m"] > -100]
# drop na gics
stocks = stocks.dropna(subset=["ggroup","gind", "gsector", "gsubind"])
# drop missing trt1m
stocks = stocks.dropna(subset=["trt1m"])

/var/folders/m6/h9jtrhyn259fytxp6j9xh9v00000gn/T/ipykernel_29303/620599596.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  stocks = pd.read_csv("data/comp_stocks.csv")


In [6]:
stocks.shape

(6394616, 22)

In [7]:
# get factors
def get_factors():

    ff_factors = pd.read_csv("data/ff_factors.csv")
    ff_factor_mom = pd.read_csv("data/ff_factor_umd.csv")
    ff_factors.rename({"Unnamed: 0": "date"}, axis=1, inplace=True)
    ff_factor_mom.rename({"Unnamed: 0": "date", "Mom":"UMD"}, axis=1, inplace=True)
    ff_factor_mom.rename({"Unnamed: 0": "date", "Mom   ":"UMD"}, axis=1, inplace=True)
    ff_factors = ff_factors.merge(ff_factor_mom, how="left", on="date")
    
    ff_factors["date"] = pd.to_datetime(ff_factors["date"], format="%Y%m")
    ff_factors["date"] += MonthEnd(0)


    return ff_factors

In [8]:
def get_company(stocks, gvkey):
    comp = stocks[stocks["gvkey"] == gvkey]
    comp = comp.drop_duplicates(subset="datadate", keep="first")
    comp = comp.set_index("datadate")
    comp.index = comp.index + MonthEnd(0)

    return comp

In [9]:
def prep_reg(cpi, comp_data, ff_factors, factor):
    
    X = cpi[["date", factor]].set_index("date")


    comp_data["Excess Return"] = comp_data["trt1m"] - ff_factors.set_index("date")["RF"]
    y = comp_data['Excess Return']

    

    # get indies that are the same between X and y
    indies_X = X.index.intersection(y.index)

    indies_y = y.index.intersection(X.index)

    indies = indies_X.intersection(indies_y)

    # save those rows
    X = X.loc[indies]
    y = y.loc[indies]
    
    return X, y

In [10]:
def run_reg(X, y):
    X = sm.add_constant(X)
    model = sm.OLS(y, X)
    results = model.fit()
    results.summary()
    return results

In [11]:
gvkeys = stocks["gvkey"].unique()

In [12]:
from tqdm import tqdm

In [13]:
# save the betas
beta_dict = {}
ff_factors = get_factors()
factor = "diff"
for company in tqdm(gvkeys):

    # supress warnings
    with warnings.catch_warnings():
        warnings.filterwarnings("ignore")
        try:
            company_data = get_company(stocks, company)
             
            if len(company_data) < 6:
                continue
            X, y = prep_reg(cpi, company_data, ff_factors, factor)
        
            
            
            if (X.shape[0] < 2) or (y.shape[0] < 2):
                continue
            
            
            reg_results = run_reg(X, y)
            beta_dict[company] = {"alpha": reg_results.params[0],"beta":reg_results.params[factor], "t-stat":reg_results.tvalues[factor]}
            
        except ValueError:
            print("ValueError for gvkey: ", company)
            break

100%|██████████| 35770/35770 [05:59<00:00, 99.59it/s] 


In [14]:
# convert dict of dict to dataframe

reg_results = pd.DataFrame.from_dict(beta_dict, orient="index")

In [15]:
#hist of t-stat and betas using plotly
fig = px.histogram(reg_results, x="t-stat", nbins=100, title="t-stat distribution")
fig.show()

fig = px.histogram(reg_results, x="beta", nbins=100, title="beta distribution")
fig.show()

fig = px.histogram(reg_results, x="alpha", nbins=100, title="alpha distribution")
fig.show()

In [16]:
# get all t stats above 2 or below -2
sig_t = reg_results[(reg_results["t-stat"] >= 2) | (reg_results["t-stat"] <= -2)]


In [17]:
companies = list(sig_t.index)

In [18]:
# get all stocks that are in companies
sig_stocks = stocks[stocks["gvkey"].isin(companies)]

In [19]:
sig_stocks.shape

(1084365, 22)

In [20]:
# save to csv
sig_stocks.to_csv("sig_stocks.csv")

In [21]:
# get the min and max date 
min_date = sig_stocks["datadate"].min()
max_date = sig_stocks["datadate"].max()

min_date, max_date

(Timestamp('1963-09-30 00:00:00'), Timestamp('2023-01-31 00:00:00'))

In [28]:
sig_t

alpha       beta    t-stat
1008    -1.085897 -39.525648 -3.701885
1062     0.744870   3.446355  3.362035
1096     0.494376   3.191853  3.590342
1121     1.399267   4.441388  2.704250
1140   -12.928431 -30.506235 -2.205080
...           ...        ...       ...
331757  -4.578263  21.473262  3.050937
338521  -5.087953  24.088444  3.178527
348615  40.973754  92.023112  2.403168
349972  -9.890643 -10.079382 -2.146132
353444 -15.511119 -34.291735 -3.541065

[4821 rows x 3 columns]

In [26]:
sig_t.shape[0]/reg_results.shape[0]

0.1352427974303588

In [23]:
reg_results

alpha       beta    t-stat
1001     2.537880   2.425855  0.377289
1003     2.423586  12.684144  1.495450
1004     1.050016   1.599466  1.320488
1007    -1.484620   4.785646  1.829873
1008    -1.085897 -39.525648 -3.701885
...           ...        ...       ...
351458  15.545189  32.430669  0.712857
351491  -5.283463 -13.978471 -1.079932
351590  -1.295765  -6.819563 -0.753141
352257   0.079879  15.566211  0.752011
353444 -15.511119 -34.291735 -3.541065

[35647 rows x 3 columns]

In [27]:
# get hist of betas of sig_t
fig = px.histogram(sig_t, x="beta", nbins=100, title="beta distribution")
fig.show()

In [88]:
# plot dates of stocks

In [75]:
# convert dict of dict to dataframe

reg_results = pd.DataFrame.from_dict(beta_dict, orient="index")

In [76]:
#hist of t-stat and betas using plotly
fig = px.histogram(reg_results, x="t-stat", nbins=100, title="t-stat distribution")
fig.show()

fig = px.histogram(reg_results, x="beta", nbins=100, title="beta distribution")
fig.show()

fig = px.histogram(reg_results, x="alpha", nbins=100, title="alpha distribution")
fig.show()

In [30]:
sig_stocks.sort_values("datadate")

gvkey iid   datadate    tic      cusip  \
1462407    8005  01 1963-09-30  4033A  668707003   
1462408    8005  01 1963-10-31  4033A  668707003   
1462409    8005  01 1963-11-30  4033A  668707003   
1002818    5848  01 1963-12-31  IBP.1  449223106   
1462410    8005  01 1963-12-31  4033A  668707003   
...         ...  ..        ...    ...        ...   
4650998   61163  02 2023-01-31    SHO  867892101   
4654253   61188  01 2023-01-31    SVC  81761L102   
1131388    6433  01 2023-01-31   KBAL  494274103   
4667556   61356  01 2023-01-31   NOVT  67000B104   
7677799  353444  90 2023-01-31    HLN  405552100   

                                 conm  dvrate      cshtrm     prccm    trfm  \
1462407              NORTON SIMON INC    0.50    113100.0   29.2498  1.0000   
1462408              NORTON SIMON INC    0.50     78500.0   27.9998  1.0000   
1462409              NORTON SIMON INC    0.50     86200.0   26.9998  1.0046   
1002818                       IBP INC     NaN         NaN   17.0000  1.0000   
1462410              NORTON SIMON INC    0.50     96100.0   27.2498  1.0046   
...                               ...     ...         ...       ...     ...   
4650998  SUNSTONE HOTEL INVESTORS INC    0.20  41489787.0   10.9900  2.0031   
4654253      SERVICE PROPERTIES TRUST    0.80  15081922.0    8.9100  8.5069   
1131388  KIMBALL INTERNATIONAL  -CL B    0.36   2287775.0    7.4000  6.3613   
4667556                   NOVANTA INC     NaN   1958802.0  161.4700  1.0000   
7677799                    HALEON PLC     NaN  76238800.0    8.1000  1.0000   

         ...         cshom  exchg        cik  ggroup      gind  gsector  \
1462407  ...           NaN    0.0    90534.0  3020.0  302020.0     30.0   
1462408  ...           NaN    0.0    90534.0  3020.0  302020.0     30.0   
1462409  ...           NaN    0.0    90534.0  3020.0  302020.0     30.0   
1002818  ...           NaN   11.0    52477.0  3020.0  302020.0     30.0   
1462410  ...           NaN    0.0    90534.0  3020.0  302020.0     30.0   
...      ...           ...    ...        ...     ...       ...      ...   
4650998  ...  2.104000e+08   11.0  1295810.0  6010.0  601010.0     60.0   
4654253  ...  1.654530e+08   14.0   945394.0  6010.0  601010.0     60.0   
1131388  ...  3.640600e+07   14.0    55772.0  2020.0  202010.0     20.0   
4667556  ...  3.569000e+07   14.0  1076930.0  4520.0  452030.0     45.0   
7677799  ...  9.234574e+09   11.0        NaN  3030.0  303020.0     30.0   

            gsubind     sic  spcindcd  spcseccd  
1462407  30202030.0  2030.0     250.0     978.0  
1462408  30202030.0  2030.0     250.0     978.0  
1462409  30202030.0  2030.0     250.0     978.0  
1002818  30202020.0  2011.0     250.0     978.0  
1462410  30202030.0  2030.0     250.0     978.0  
...             ...     ...       ...       ...  
4650998  60101030.0  6798.0     850.0     800.0  
4654253  60101030.0  6798.0     850.0     800.0  
1131388  20201060.0  2520.0     370.0     925.0  
4667556  45203010.0  3679.0     247.0     940.0  
7677799  30302010.0  2834.0       NaN       NaN  

[1084365 rows x 22 columns]